In [ ]:
# Installs required library
!pip install hvplot holoviews

     |████████████████████████████████| 3.1 MB 11.7 MB/s 


In [ ]:
# Installs required library
!pip install finta

In [ ]:
# Imports required libraries and dependencies
import pandas as pd
import numpy as np
import hvplot.pandas
from pathlib import Path
import matplotlib.pyplot as plt
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from pandas.tseries.offsets import DateOffset
from sklearn.metrics import classification_report
from finta import TA


In [ ]:
# Specifies the max_rows, max_columns, and width values
pd.set_option('display.max_rows', 2000)
pd.set_option('display.max_columns', 2000)
pd.set_option('display.width', 1000)


In [ ]:
# Uploads the "Bitstamp_BTCUSD_d(1).csv" file into Colab
from google.colab import files

csv_file = files.upload()

Saving BTCUSD_4h.csv to BTCUSD_4h.csv


In [ ]:
# Reads the "Bitstamp_BTCUSD_d(1).csv" into the Pandas DataFrame aand sets the 
# date column as the DatetimeIndex
btc_df = pd.read_csv(
    Path("/content/BTCUSD_4h.csv"),
    index_col = "Date", 
    parse_dates = True, 
    infer_datetime_format = True
)

In [ ]:
# Calculates the daily returns using the closing prices the pct_change function
# Values are assigned to a new column, "actual_returns"
# Drops any NA values in the DataFrame
btc_df["actual_returns"] = btc_df["Close"].pct_change()
btc_df = btc_df.dropna()

# Defines a window size of 4
# Returns a Series object within the DataFrame with a SMA that uses 
# the short_window of 4 and assigns it to a new column, 'sma_fast'
short_window = 4
btc_df['sma_fast'] = TA.SMA(btc_df, 4)

# Defines a long window size of 100
# Creates a SMA that uses the long_window and assigns it to a new column
# column, 'sma_slow'
long_window = 100
btc_df['sma_slow'] = btc_df['Close'].rolling(window=long_window).mean()

#
btc_df["ssma"] = TA.SSMA(btc_df)
btc_df["ema"] = TA.EMA(btc_df, 50)
btc_df["dema"] = TA.DEMA(btc_df)
btc_df["tema"] = TA.TEMA(btc_df)
btc_df["trima"] = TA.TRIMA(btc_df)

# Drops any NA values in the DataFrame
btc_df = btc_df.dropna()

# Assigns a copy of the sma_fast', 'sma_slow', 'ssma', 'ema', 'dema', 'tema', 'trima'
# columns to a new DataFrame called 'X'
X = btc_df[['sma_fast', 'sma_slow', 'ssma', 'ema', 'dema', 'tema', 'trima']].shift().dropna().copy()

# Creates a new column in the 'btc_df' called 'signal' 
# Value set to 0.0
btc_df['signal'] = 0.0

# Creates buy and sell signals
# Display last 3 rows of DataFrame
btc_df.loc[(btc_df['actual_returns'] >= 0), 'signal'] = 1
btc_df.loc[(btc_df['actual_returns'] < 0), 'signal'] = -1
btc_df.tail(3)

# 
y = btc_df['signal']
display(X.head(5))
display(y.head(2))

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # This is added back by InteractiveShellApp.init_path()
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the

sma_fast      sma_slow          ssma           ema          dema          tema         trima
Date                                                                                                                 
2018-01-17 20:00:00  10191.217729  14247.730138  11653.741599  13025.233845   9937.935076   9778.656241  13338.219035
2018-01-18 00:00:00  10248.964377  14222.570138  11593.103230  12948.702165  10207.749469  10260.376508  13238.434024
2018-01-18 04:00:00  10577.825000  14202.400138  11550.980394  12879.505323  10454.600703  10648.582193  13132.275557
2018-01-18 08:00:00  10836.250000  14175.720138  11438.648634  12786.245894  10400.321464  10583.442363  13016.765237
2018-01-18 12:00:00  11081.000000  14157.850138  11441.243243  12733.491776  10703.089893  11001.368634  12894.603683

Date
2018-01-17 16:00:00    1.0
2018-01-17 20:00:00    1.0
Name: signal, dtype: float64

In [ ]:
# Reviews the DataFrame
btc_df.head()

Open    Close     High      Low        Volume  actual_returns      sma_fast      sma_slow          ssma           ema          dema          tema         trima  signal
Date                                                                                                                                                                                           
2018-01-17 16:00:00   9512.0  10483.0  10643.0   9493.0  21091.217332        0.102742  10191.217729  14247.730138  11653.741599  13025.233845   9937.935076   9778.656241  13338.219035     1.0
2018-01-17 20:00:00  10480.0  11108.0  11450.0  10351.0  24765.890715        0.059620  10248.964377  14222.570138  11593.103230  12948.702165  10207.749469  10260.376508  13238.434024     1.0
2018-01-18 00:00:00  11113.0  11214.0  11670.0  10775.0  19111.388632        0.009543  10577.825000  14202.400138  11550.980394  12879.505323  10454.600703  10648.582193  13132.275557     1.0
2018-01-18 04:00:00  11217.0  10540.0  11456.0  10515.0  12891.019321       -0.060103  10836.250000  14175.720138  11438.648634  12786.245894  10400.321464  10583.442363  13016.765237    -1.0
2018-01-18 08:00:00  10539.0  11462.0  11608.0  10515.0  11873.272205        0.087476  11081.000000  14157.850138  11441.243243  12733.491776  10703.089893  11001.368634  12894.603683     1.0

In [ ]:
# Import DateOffset Module
from pandas.tseries.offsets import DateOffset

# Selects start of training period
training_begin = X.index.min()
print(training_begin)

# Selects end of training period with an offset of 1 month
training_end = X.index.min() + DateOffset(months=1)
print(training_end)

# Creates the X_train and y_train DataFrames
X_train = X.loc[training_begin:training_end]
y_train = y.loc[training_begin:training_end]

# Creates the X_test and y_test DataFrames
X_test = X.loc[training_end:]
y_test = y.loc[training_end:]

2018-01-17 20:00:00
2018-02-17 20:00:00


In [ ]:
# Imports StandardScaler module
from sklearn.preprocessing import StandardScaler

# Creates StandardScaler instance
scaler = StandardScaler()

# Applies the scaler model to the the X_train data
X_scaler = scaler.fit(X_train)

# Transforms the X_train and X_test DataFrames using X_scaler
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [ ]:
# Imports RandomOverSampler Module
from imblearn.over_sampling import RandomOverSampler

# Resamples data
ros = RandomOverSampler(random_state=1)
X_resampled, y_resampled = ros.fit_resample(X_train_scaled, y_train)

In [ ]:
# Uses hvplot to visualize 'Close' price
btc_df["Close"].hvplot()

:Curve   [Date]   (Close)

In [ ]:

#
signals_df = btc_df.loc[:, ["Close"]].copy()

# Sets short_window period to 50
short_window = 50

#
signals_df["SMA50"] = signals_df["Close"].rolling(window=short_window).mean()

#
signals_df["EMA50"] = signals_df["Close"].ewm(span=short_window).mean()

#
signals_df.iloc[45:55, :]

Close         SMA50         EMA50
Date                                                    
2018-01-25 04:00:00  11403.0           NaN  11258.961361
2018-01-25 08:00:00  11171.0           NaN  11254.890946
2018-01-25 12:00:00  10978.0           NaN  11242.167628
2018-01-25 16:00:00  11229.0           NaN  11241.566615
2018-01-25 20:00:00  11147.0  11330.081935  11237.277855
2018-01-26 00:00:00  11529.0  11351.001935  11250.427276
2018-01-26 04:00:00  11018.0  11349.201935  11240.011610
2018-01-26 08:00:00  10485.0  11334.621935  11206.365905
2018-01-26 12:00:00  11026.0  11344.341935  11198.370982
2018-01-26 16:00:00  10903.0  11333.161935  11185.344899

In [ ]:
# Uses hvplot to visualize close price of trade
security_close = signals_df[["Close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

# Uses hvplot to Visualize moving averages
moving_avgs = signals_df[["SMA50", "EMA50"]].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Creates and displays overlay plot
sma_ema_plot = security_close * moving_avgs
sma_ema_plot

:Overlay
   .Curve.I     :Curve   [Date]   (Close)
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [Date]   (value)

In [ ]:

ema_signals_df = btc_df.loc[:, ["Close"]].copy()

# Creates short_window and lond_window periods
short_window = 50
long_window = 100

# Generates the short and long window exponential moving averages
ema_signals_df["EMA50"] = signals_df["Close"].ewm(span=short_window).mean()
ema_signals_df["EMA100"] = signals_df["Close"].ewm(span=long_window).mean()

# Reviews DataFrame
ema_signals_df.head()

Close         EMA50        EMA100
Date                                                    
2018-01-17 16:00:00  10483.0  10483.000000  10483.000000
2018-01-17 20:00:00  11108.0  10801.750000  10798.625000
2018-01-18 00:00:00  11214.0  10944.699240  10939.861638
2018-01-18 04:00:00  10540.0  10837.374652  10836.877475
2018-01-18 08:00:00  11462.0  10972.489469  10966.952461

In [ ]:
# Creates a column to hold trading signal
ema_signals_df["Signal"] = 0.0

# Generates the trading signal 0.0 or 1.0
# where 1.0 is the short-window (EMA50) greater than the long-window (EMA100)
# and 0 is when the condition is not met
ema_signals_df["Signal"][short_window:] = np.where(
    ema_signals_df["EMA50"][short_window:] > ema_signals_df["EMA100"][short_window:], 1.0, 0.0
)

# Calculates the points in time when the Signal value changes
# Indentifies trade entry and exit points
ema_signals_df["Entry/Exit"] = ema_signals_df["Signal"].diff()

# Reviews the DataFrame
ema_signals_df.head()

Close         EMA50        EMA100  Signal  Entry/Exit
Date                                                                        
2018-01-17 16:00:00  10483.0  10483.000000  10483.000000     0.0         NaN
2018-01-17 20:00:00  11108.0  10801.750000  10798.625000     0.0         0.0
2018-01-18 00:00:00  11214.0  10944.699240  10939.861638     0.0         0.0
2018-01-18 04:00:00  10540.0  10837.374652  10836.877475     0.0         0.0
2018-01-18 08:00:00  11462.0  10972.489469  10966.952461     0.0         0.0

In [ ]:
# Uses hvplot to visualize the entry position relative to 'Close' price
entry = ema_signals_df[ema_signals_df["Entry/Exit"] == 1.0]["Close"].hvplot.scatter(
    color='purple',
    marker='^',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Uses hvplot to visualize the exit position relative to 'Close' price
exit = ema_signals_df[ema_signals_df["Entry/Exit"] == -1.0]["Close"].hvplot.scatter(
    color='orange',
    marker='v',
    size=200,
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400
)

# Uses hvplot to visualize close price for the trade
security_close = ema_signals_df[["Close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)


# Uses hvplot to visualize EMAs
moving_avgs = ema_signals_df[["EMA50", "EMA100"]].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400
)

# Creates and displays the overlay plot 
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot

:Overlay
   .Curve.I          :Curve   [Date]   (Close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.Close.I  :Scatter   [Date]   (Close)
   .Scatter.Close.II :Scatter   [Date]   (Close)

In [ ]:
bb_signals_df = btc_df.copy()
bb_signals_df.head()


Open    Close     High      Low        Volume  actual_returns      sma_fast      sma_slow          ssma           ema          dema          tema         trima  signal
Date                                                                                                                                                                                           
2018-01-17 16:00:00   9512.0  10483.0  10643.0   9493.0  21091.217332        0.102742  10191.217729  14247.730138  11653.741599  13025.233845   9937.935076   9778.656241  13338.219035     1.0
2018-01-17 20:00:00  10480.0  11108.0  11450.0  10351.0  24765.890715        0.059620  10248.964377  14222.570138  11593.103230  12948.702165  10207.749469  10260.376508  13238.434024     1.0
2018-01-18 00:00:00  11113.0  11214.0  11670.0  10775.0  19111.388632        0.009543  10577.825000  14202.400138  11550.980394  12879.505323  10454.600703  10648.582193  13132.275557     1.0
2018-01-18 04:00:00  11217.0  10540.0  11456.0  10515.0  12891.019321       -0.060103  10836.250000  14175.720138  11438.648634  12786.245894  10400.321464  10583.442363  13016.765237    -1.0
2018-01-18 08:00:00  10539.0  11462.0  11608.0  10515.0  11873.272205        0.087476  11081.000000  14157.850138  11441.243243  12733.491776  10703.089893  11001.368634  12894.603683     1.0

In [ ]:
bbands_df = TA.BBANDS(bb_signals_df)
bbands_df.iloc[17:25, :]

BB_UPPER  BB_MIDDLE      BB_LOWER
Date                                                      
2018-01-20 12:00:00           NaN        NaN           NaN
2018-01-20 16:00:00           NaN        NaN           NaN
2018-01-20 20:00:00  12951.705345   11574.85  10197.994655
2018-01-21 00:00:00  13004.270253   11673.90  10343.529747
2018-01-21 04:00:00  13021.593345   11714.55  10407.506655
2018-01-21 08:00:00  13056.500201   11759.80  10463.099799
2018-01-21 12:00:00  12979.923546   11805.20  10630.476454
2018-01-21 16:00:00  12980.187039   11804.20  10628.212961

In [ ]:
bb_signals_df = pd.concat([bb_signals_df, bbands_df], axis=1)


bb_signals_df.iloc[17:25, :]

Open    Close     High           Low        Volume  actual_returns  sma_fast      sma_slow          ssma           ema          dema          tema         trima  signal      BB_UPPER  BB_MIDDLE      BB_LOWER
Date                                                                                                                                                                                                                                   
2018-01-20 12:00:00  12297.0  12515.0  12699.0  12251.000000   5412.992110        0.017893  12278.50  13802.610138  11725.653253  12305.262034  12295.771207  12539.668966  11361.501561     1.0           NaN        NaN           NaN
2018-01-20 16:00:00  12520.0  12736.0  13017.0  12517.000000  10019.677176        0.017659  12537.25  13779.420138  11837.914106  12322.305569  12516.046521  12755.155424  11328.277313     1.0           NaN        NaN           NaN
2018-01-20 20:00:00  12738.0  12732.0  12950.0  12583.000000   3785.238535       -0.000314  12569.50  13758.790138  11937.257065  12338.510737  12664.380861  12869.191811  11307.627138    -1.0  12951.705345   11574.85  10197.994655
2018-01-21 00:00:00  12731.0  12464.0  12732.0  12307.000000   6501.302502       -0.021049  12611.75  13738.150138  11995.784100  12343.472694  12665.539604  12789.080443  11297.754742    -1.0  13004.270253   11673.90  10343.529747
2018-01-21 04:00:00  12461.0  11921.0  12488.0  11663.000000  12548.194212       -0.043565  12463.25  13712.700138  11987.474750  12326.773178  12462.739615  12453.224364  11301.582963    -1.0  13021.593345   11714.55  10407.506655
2018-01-21 08:00:00  11922.0  12119.0  12119.0  11621.000000   7267.558094        0.016609  12309.00  13684.140138  12002.088675  12318.562877  12382.558038  12322.234229  11314.590196     1.0  13056.500201   11759.80  10463.099799
2018-01-21 12:00:00  12119.0  11448.0  12223.0  11411.392312   8355.901790       -0.055368  11988.00  13647.030138  11940.523236  12284.172300  12079.139507  11904.652559  11333.757923    -1.0  12979.923546   11805.20  10630.476454
2018-01-21 16:00:00  11449.0  11442.0  11593.0  11155.000000  10649.200887       -0.000524  11732.50  13612.210138  11885.131740  12250.912843  11857.546067  11634.847295  11359.163304    -1.0  12980.187039   11804.20  10628.212961

In [ ]:
security_close = bb_signals_df[["Close"]].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400
)

bb_upper = bb_signals_df[["BB_UPPER"]].hvplot(
    line_color='purple',
    ylabel='Price in $',
    width=1000,
    height=400
)


bb_middle = bb_signals_df[["BB_MIDDLE"]].hvplot(
    line_color='orange',
    ylabel='Price in $',
    width=1000,
    height=400
)

bb_lower = bb_signals_df[["BB_LOWER"]].hvplot(
    line_color='blue',
    ylabel='Price in $',
    width=1000,
    height=400
)


# Creates and displays overlay plots
bbands_plot = security_close * bb_upper * bb_middle * bb_lower
bbands_plot

:Overlay
   .Curve.I   :Curve   [Date]   (Close)
   .Curve.II  :Curve   [Date]   (BB_UPPER)
   .Curve.III :Curve   [Date]   (BB_MIDDLE)
   .Curve.IV  :Curve   [Date]   (BB_LOWER)

In [ ]:
btc_df["Signal"] = 0.0


for index, row in btc_df.iterrows():
    if row["Close"] < row["BB_LOWER"]:
        btc_df.loc[index, "Signal"] = 1.0
    if row["Close"] > row["BB_UPPER"]:
        btc_df.loc[index,"Signal"] = -1.0


btc_df

KeyError: ignored